In [3]:
from bs4 import BeautifulSoup
import re
import requests
import fake_useragent
import json
import csv
import random
import time
import os
import json
import pandas as pd

ua = fake_useragent.UserAgent( )

headers = {
    "Accept": "*/*",
    "User-Agent": ua.ie,
    "Accept-Language": "ru-RU,ru;q=0.9,en-US;q=0.8,en;q=0.7"
}

In [ ]:
#ПОЛУЧИТЬ ПРАМЕТРЫ ДАТЧИКОВ
category_name = 'Индуктивные датчики'
category_href = 'https://skbind.ru/catalog/induktivnye_datchiki/'


with open(f'data/{category_name}_SKB.csv', 'w', encoding = 'utf-8', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(('category_name','sensor_type','sensor_symbol',
                     'sensor_url','sensor_imgurl','sensor_price','sensor_in_stock'))

count = 0
pages = 65
for i in range(1,pages):    
    url_page = category_href + '?PAGEN_1=' + f'{i}'
    res = requests.get(url_page, headers=headers)
    soup = BeautifulSoup(res.content, 'lxml')
    sensor_list = soup.find_all('div', class_="inner_wrap TYPE_1")
    if len(sensor_list) == 0:
        break
    
    for sensor in sensor_list:
        sensor_bare_name = sensor.find('div', class_="item-title").text.strip()
        try:
            options = re.findall(r'(\(.+\))', sensor_bare_name)[0]
        except:
            options = ''
        sensor_symbol = sensor_bare_name.replace(options, '').strip()       # Промежуточный вариант
        sensor_type = re.findall(r'[А-Яа-яёЁ]{5,20}\s*"?N?A?M?U?R?"?', sensor_symbol)
        for word in sensor_type: sensor_symbol = sensor_symbol.replace(word, '').strip()
        sensor_symbol = sensor_symbol + ' ' + options
        sensor_type = ''.join(sensor_type).strip()
        
        sensor_url = 'https://skbind.ru' + sensor.find('a').get("href")
        try:
            sensor_imgurl = 'https://skbind.ru' + sensor.find('img', class_="lazy img-responsive").get("src")
        except:
            sensor_imgurl = None
        sensor_price = None
        sensor_in_stock = None
        count += 1
        print (f'{count}) {category_name}, {sensor_type}, {sensor_symbol} {sensor_url}')#, {sensor_imgurl}, {sensor_price}, {sensor_in_stock}')

        with open(f'data/{category_name}_SKB.csv', 'a', encoding = 'utf-8', newline='') as file:
            writer = csv.writer(file)
            writer.writerow((category_name, sensor_type, sensor_symbol, sensor_url, sensor_imgurl, sensor_price, sensor_in_stock))
        
    time.sleep(random.randrange(2,12))

In [62]:
#СОХРАНИТЬ ПАРАМЕТРЫ ДАТЧИКОВ С КАЖДОЙ СТРАНИЦЫ
import pandas as pd

def getparams(parameters):
    for item in parameters:
        parameter = item.find('div', class_='properties__title').get_text().replace('\t', '').strip()
        value = item.find('div', class_='properties__value').get_text().strip()
        parameters_dict[parameter] = value
    return parameters_dict

with open(f'data/Индуктивные датчики_SKB.csv', encoding = 'utf-8') as f:
    df_skb = pd.read_csv(f)
    
df_skb.drop_duplicates(subset=['sensor_url'], keep='first', inplace=True)

# df_skb = df_skb.assign(param = None)
parameters_dict = {}

for index, row in df_skb.iterrows():
    # print(index, df_skb.loc [index, 'param'])
    if not df_skb['param'].isnull()[index]:
        continue
    param_req = requests.get(row['sensor_url'], headers=headers)
    param_soup = BeautifulSoup(param_req.content, 'lxml')
    
    parameters = param_soup.find_all('div', class_="properties__item properties__item--dotted")
    parameters_dict = getparams(parameters)
    
    parameters_dict['additional'] = [param.get_text() for param in param_soup.find_all('span', class_="breadcrumbs__item-name font_xs")]

    df_skb.loc [df_skb.index == index, 'param'] = json.dumps(parameters_dict)
    print(index, df_skb.loc [index, 'param'])
    
    time.sleep(random.randrange(2,4))

df_skb.to_csv('data/Индуктивные датчики_SKB.csv', index=False)

3382 {"\u0422\u0438\u043f\u043e\u0440\u0430\u0437\u043c\u0435\u0440 \u043a\u043e\u0440\u043f\u0443\u0441\u0430, \u043c\u043c": "\u0426\u0438\u043b\u0438\u043d\u0434\u0440\u0438\u0447\u0435\u0441\u043a\u0438\u0439 \u0441 \u0440\u0435\u0437\u044c\u0431\u043e\u0439, \u041c30x1,5", "\u041c\u0430\u0442\u0435\u0440\u0438\u0430\u043b \u043a\u043e\u0440\u043f\u0443\u0441\u0430 \u0434\u0430\u0442\u0447\u0438\u043a\u0430": "\u041b\u0430\u0442\u0443\u043d\u044c", "\u041c\u0430\u0442\u0435\u0440\u0438\u0430\u043b \u0433\u0430\u0439\u043a\u0438": "\u041f\u043e \u0437\u0430\u043f\u0440\u043e\u0441\u0443", "\u0421\u043f\u043e\u0441\u043e\u0431 \u0443\u0441\u0442\u0430\u043d\u043e\u0432\u043a\u0438": "\u0412\u0441\u0442\u0440\u0430\u0438\u0432\u0430\u0435\u043c\u044b\u0439", "\u041c\u043e\u043c\u0435\u043d\u0442 \u0437\u0430\u0442\u044f\u0436\u043a\u0438 \u043a\u0440\u0435\u043f\u0435\u0436\u0430, \u041d\u043c, \u043d\u0435 \u0431\u043e\u043b\u0435\u0435": "50", "\u0421\u0445\u0435\u043c\u0430 \u0432\

In [ ]:
#ДОПИСАТЬ ПОЛЕ ОПШИНС В ОБОЗНАЧЕНИЕ
category_name = 'Индуктивные датчики'
category_href = 'https://skbind.ru/catalog/induktivnye_datchiki/'

count = 0
pages = 65
for i in range(1,pages):    
    url_page = category_href + '?PAGEN_1=' + f'{i}'
    res = requests.get(url_page, headers=headers)
    soup = BeautifulSoup(res.content, 'lxml')
    sensor_list = soup.find_all('div', class_="inner_wrap TYPE_1")
    if len(sensor_list) == 0:
        print('КОНЕЦ')
        break
    
    for sensor in sensor_list:
        sensor_bare_name = sensor.find('div', class_="item-title").text.strip()
        try:
            options = re.findall(r'(\(.+\))', sensor_bare_name)[0]
        except:
            options = ''
        sensor_symbol = sensor_bare_name.replace(options, '').strip()       # Промежуточный вариант
        sensor_type = re.findall(r'[А-Яа-яёЁ]{5,20}\s*"?N?A?M?U?R?"?', sensor_symbol)
        for word in sensor_type: sensor_symbol = sensor_symbol.replace(word, '').strip()
        
        sensor_url = 'https://skbind.ru' + sensor.find('a').get("href")
        
        df_skb.loc[df_skb["sensor_url"] == sensor_url, 'sensor_symbol'] = sensor_symbol + ' ' + options
        print (count, sensor_symbol + ' ' + options)
        count += 1

    time.sleep(random.randrange(2,5))

In [17]:
my_str = json.dumps(parameters_dict)
print (my_str)
json.loads(my_str)
# for index, row in df_skb.iterrows():
#     print (type(json.loads(row[ 'param'])))

{"\u0422\u0438\u043f\u043e\u0440\u0430\u0437\u043c\u0435\u0440 \u043a\u043e\u0440\u043f\u0443\u0441\u0430, \u043c\u043c": "\u0426\u0438\u043b\u0438\u043d\u0434\u0440\u0438\u0447\u0435\u0441\u043a\u0438\u0439 \u0441 \u0440\u0435\u0437\u044c\u0431\u043e\u0439, \u041c30x1,5", "\u041c\u0430\u0442\u0435\u0440\u0438\u0430\u043b \u043a\u043e\u0440\u043f\u0443\u0441\u0430 \u0434\u0430\u0442\u0447\u0438\u043a\u0430": "\u041b\u0430\u0442\u0443\u043d\u044c", "\u041c\u0430\u0442\u0435\u0440\u0438\u0430\u043b \u0433\u0430\u0439\u043a\u0438": "\u041b\u0430\u0442\u0443\u043d\u044c", "\u041c\u043e\u043c\u0435\u043d\u0442 \u0437\u0430\u0442\u044f\u0436\u043a\u0438 \u043a\u0440\u0435\u043f\u0435\u0436\u0430, \u041d\u043c, \u043d\u0435 \u0431\u043e\u043b\u0435\u0435": "50", "\u0421\u0445\u0435\u043c\u0430 \u0432\u044b\u0445\u043e\u0434\u0430": "AC 2-\u0445 \u043f\u0440.", "\u0424\u0443\u043d\u043a\u0446\u0438\u044f \u0432\u044b\u0445\u043e\u0434\u0430": "NO", "\u041d\u0430\u043b\u0438\u0447\u0438\u0435 \

In [6]:
def getimage(url, index, df_skb):
    if df_skb['sensor_imgurl'].isnull()[index]:
        return '/static/main/img/ind_SKB/SKBIND.png'
    file_name = url.split('/')[-1]
    if file_name == 'noimage_product.svg':
        return '/static/main/img/ind_SKB/SKBIND.png'
    file_adr = '../main/static/main/img/ind_SKB/' + file_name
    if not os.path.exists(file_adr):
        time.sleep(random.randrange(4,10))
        img_data = requests.get(url).content
        with open(file_adr, 'wb') as handler:
            handler.write(img_data)
    return '/static/main/img/ind_SKB/' + file_name


In [4]:
def getsensortype(parameters_dict):
    for word in parameters_dict.get('additional'):
        if 'Аналоговые' in word:
            return 'Индуктивный преобразователь перемещения'
        if 'cкорости' in word:
            return 'Датчик скорости'
    return 'Индуктивный датчик'

def getflush(parameters_dict):
    for word in parameters_dict.get('additional'):
        if 'И09-NC-AC-Z(Л63, Lкаб=5м)' in word:
            return 'Встраиваемый'
    return str(parameters_dict.get('Способ установки')).replace('Встраиваемый (неутапливаемый)*', 'Псевдовстраиваемый')

def getspecapplication(parameters_dict):
    for word in parameters_dict.get('additional'):
        if 'давления' in word:
            return 'В среде высокого давления'
        if 'NAMUR' in word:
            return 'Во взрывоопасных зонах (NAMUR)'
    return 'Общее применение'


def getoutputstructure(parameters_dict):
    if 'PNP' in parameters_dict.get('Схема выхода'):
        return 'PNP'
    if 'NPN' in parameters_dict.get('Схема выхода'):
        return 'NPN'
    if 'реле' in parameters_dict.get('Схема выхода'):
        return 'Реле'
    if '2-х пр' in parameters_dict.get('Схема выхода'):
        return 'Двухпроводный датчик'
    if 'NDC' in parameters_dict.get('Схема выхода'):
        return 'Двухпроводный датчик'
    if re.search (r'^U', parameters_dict.get('Функция выхода')):
        return 'PNP'
    if re.search (r'I$', parameters_dict.get('Функция выхода')):
        return 'PNP'
    if re.search (r'I/U', parameters_dict.get('Функция выхода')):
        return 'PNP'
    for word in parameters_dict.get('additional'):
        if 'NAMUR' in word:
            return 'NAMUR'
    return None

def getoutputtype(parameters_dict):
    outputtype = str(parameters_dict.get('Функция выхода'))
    if outputtype == 'NC' or outputtype == 'NO':
        return outputtype
    if 'NO/NC' in outputtype:
        return 'NO и NC'
    if re.search (r'^U', outputtype):
        return 'Напряжение'
    if re.search (r'I$', outputtype):
        return 'Ток'
    if re.search (r'I/U', outputtype):
        return 'Напряжение и ток'
    if 'NAMUR' in outputtype:
        return 'NC'
    return outputtype

def getadjust(parameters_dict):
    if parameters_dict.get('Наличие регулировки Sn') == 'Есть' or parameters_dict.get('Наличие регулировки Sn') ==  'Нет':
        return parameters_dict.get('Наличие регулировки Sn')
    else:
        for word in parameters_dict.get('additional'):
            if 'с регулировкой' in word:
                return 'Есть'
        return 'Нет'

def getindicator(parameters_dict):
    if parameters_dict.get('Наличие индикации включения') == 'Есть' or parameters_dict.get('Наличие индикации включения') ==  'Нет':
        return parameters_dict.get('Наличие индикации включения')
    else:
        return None
    
def getdistance(parameters_dict):
    if parameters_dict.get('Номинальное расстояние переключения, Sn, мм') == '0…(70 -110)':
        return '110'
    if parameters_dict.get('Номинальное расстояние переключения, Sn, мм') == '40...120':
        return '120'
    for word in parameters_dict.get('additional'):
        if 'И09-NC-AC-Z(Л63, Lкаб=5м)' in word:
            return '5'
    return parameters_dict.get('Номинальное расстояние переключения, Sn, мм')

def getconnection(parameters_dict):
    if parameters_dict.get('Способ подключения') == 'Клеммник':
        return 'Клеммы'
    return parameters_dict.get('Способ подключения')

def getvoltage(parameters_dict):
    if parameters_dict.get('Диапазон питающих напряжений, В') == '7,7-9,0[DC]':
        return '7,7-9,0 [DC] (NAMUR)'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '20-250[AC ] 30-250[DC ]':
        return '30-250 [DC] / 20-250 [AC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '20-250[AC ] 20-310[DC ]':
        return '20-310 [DC] / 20-250 [AC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '20-250[AC ] 20-250[DC ]':
        return '20-250 [DC] / 20-250 [AC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '198-250[AC ]':
        return '198-250 [AC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '18-36[DC ]':
        return '18-36 [DC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '18-30[DC ]':
        return '18-30 [DC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '15-30[DC]':
        return '15-30 [DC]'
    if parameters_dict.get('Диапазон питающих напряжений, В') == '10-30[DC]':
        return '10-30 [DC]'    
    if parameters_dict.get('Диапазон питающих напряжений, В') == '16-30[DC ]':
        return '16-30 [DC]'    
    if parameters_dict.get('Диапазон питающих напряжений, В') == '20-30[DC ]':
        return '20-30 [DC]'    
    for word in parameters_dict.get('additional'):
        if 'И09-NC-AC-Z(Л63, Lкаб=5м)' in word:
            return '30-250 [DC] / 20-250 [AC]'
    return parameters_dict.get('Диапазон питающих напряжений, В')


def gettemperature(parameters_dict):
    temper = parameters_dict.get('Рабочая температура окружающей среды, °С')
    temper = temper.replace('…', '...')
# -10…+50, -15…+105, -25…+75, -40…+65, -45…+65, -55…+65, -60…+65, +15...+35, 0…+50
    return temper

def getsize(parameters_dict):
    size = parameters_dict.get('Типоразмер корпуса, мм').split(',', maxsplit=1)[-1]
    size = size.strip()
    match = re.search(r"^[MМ](\d+)[xх].+", size)
    if match:
        return '∅' + match.group(1)
    if 'Ø' in size:
        return size.replace('Ø','∅')
    
    if size == '130х70х28':
        return '130х75х29'
    if size == '40х40х127':
        return '40х40х130'
    if size == '60х50х40':
        return '60х60х40'
    
    return size


In [7]:
# СОЗДАНИЕ И ЗАПОЛНЕНИЕ ПОЛЕЙ С ПАРАМЕТРАМИ ДАТЧИКОВ
with open(f'data/Индуктивные датчики_SKB.csv', encoding = 'utf-8') as f:
    df_skb = pd.read_csv(f)
    

    
df_skb = df_skb.assign(manufacturer = 'СКБ Индукция' ,
                       flush = None,
                       spec = None,
                       housing = None,
                       connection = None,
                       size = None,
                       material = None,
                       IP = None,
                       output_structure = None,
                       voltage = None,
                       output_type = None,
                       adjust = None,
                       distance = None,
                       indicator = None,
                       temperature = None)

for index, row in df_skb.iterrows():
    parameters_dict = {}
    parameters_dict = json.loads(row ['param'])

    print(index, parameters_dict)
    df_skb.loc[df_skb.index == index, 'sensor_type'] = getsensortype(parameters_dict)
    df_skb.loc[df_skb.index == index, 'flush'] = getflush(parameters_dict)
    df_skb.loc[df_skb.index == index, 'spec'] = getspecapplication(parameters_dict)
    df_skb.loc[df_skb.index == index, 'housing'] = parameters_dict.get('Типоразмер корпуса, мм').split(',', maxsplit=1)[0].replace('Цилиндрический без резьбы', 'Цилиндрический гладкий')
    df_skb.loc[df_skb.index == index, 'size'] = getsize(parameters_dict)
    df_skb.loc[df_skb.index == index, 'connection'] = getconnection(parameters_dict)
    df_skb.loc[df_skb.index == index, 'material'] = str(parameters_dict.get('Материал корпуса датчика')).replace('Пластик + сталь', 'Нерж. сталь').replace('Нержавеющая сталь','Нерж. сталь')
    df_skb.loc[df_skb.index == index, 'IP'] = str(parameters_dict.get('Степень защиты IP')).replace('IP 68/ IP 67', 'IP 68')
    df_skb.loc[df_skb.index == index, 'output_structure'] = getoutputstructure(parameters_dict)
    df_skb.loc[df_skb.index == index, 'output_type'] = getoutputtype(parameters_dict)
    df_skb.loc[df_skb.index == index, 'adjust'] = getadjust(parameters_dict)
    df_skb.loc[df_skb.index == index, 'distance'] = getdistance(parameters_dict)
    df_skb.loc[df_skb.index == index, 'indicator'] = getindicator(parameters_dict)
    df_skb.loc[df_skb.index == index, 'temperature'] = gettemperature(parameters_dict)
    df_skb.loc[df_skb.index == index, 'voltage'] = getvoltage(parameters_dict)

    df_skb.loc[index, 'sensor_imgurl'] = getimage(row['sensor_imgurl'], index, df_skb)

    print ('        ', df_skb ['sensor_symbol'][index])

df_skb['distance'] = df_skb['distance'].str.replace(',','.').astype(float)

df_skb.drop_duplicates(subset=['sensor_symbol'], keep='first', inplace=True)

df_skb.drop(columns='param', inplace=True)


df_skb = df_skb.reindex(columns=['category_name', 'sensor_type', 'sensor_symbol', 'sensor_url', 'sensor_imgurl',
                         'sensor_price', 'sensor_in_stock', 'manufacturer', 'flush', 'spec', 'housing',
                         'connection', 'size', 'material', 'IP','output_structure','voltage',
                         'output_type','adjust','distance','indicator','temperature'])

new_columns = {'category_name': 'category',
               'sensor_type': 'type',
               'sensor_symbol': 'name',
               'sensor_url': 'url',
               'sensor_imgurl': 'url_img',
               'sensor_price': 'price',
               'sensor_in_stock': 'stock',
               }

df_skb = df_skb.rename(columns=new_columns)

df_skb.to_csv('data/Индуктивные датчики SKB Ind dataframe.csv', index=False)

0 {'Типоразмер корпуса, мм': 'Цилиндрический с резьбой, М18x1', 'Материал корпуса датчика': 'Латунь', 'Материал гайки': 'Латунь', 'Момент затяжки крепежа, Нм, не более': '18', 'Схема выхода': 'AC 2-х пр.', 'Функция выхода': 'NC', 'Наличие регулировки Sn': 'Нет', 'Наличие индикации включения': 'Есть', 'Наличие защиты от переполюсовки': 'Есть', 'Наличие комплексной защиты': 'Есть', 'Наличие заземления': 'Есть', 'Способ подключения': 'Кабель', 'Длина кабеля, м': '5', 'Тип кабеля': 'ПМВ 3x0,34 мм²', 'Рабочая температура окружающей среды, °С': '-25…+75', 'Степень защиты IP': 'IP 67', 'additional': ['Главная', 'Каталог', 'Индуктивные датчики', 'Индуктивные датчики на переменное 20-250В / постоянное напряжение 30-250В', 'Выключатель бесконтактный индуктивный  И09-NC-AC-Z(Л63, Lкаб=5м)']}
         И09-NC-AC-Z (Л63, Lкаб=5м)
1 {'Типоразмер корпуса, мм': 'Цилиндрический с резьбой, М30x1,5', 'Материал корпуса датчика': 'Латунь', 'Материал гайки': 'Латунь', 'Момент затяжки крепежа, Нм, не более': 

In [ ]:
# df_skb._duplicates['name'](subset=['sensor_url'], keep='first', inplace=True)
# df_skb[df_skb.duplicated(['name'])].count()

In [217]:
    
#         'category_name', 'sensor_type', 'sensor_symbol', 'sensor_url', 'sensor_imgurl', 
#         'sensor_price', 'sensor_in_stock', 'manufacturer', 'flush', 'spec', 'housing', 'connection', 
#         'size','material','IP','output_structure','voltage','output_type','adjust','distance','indicator','temperature'

# df_skb['output_type'].unique()



array(['NC', 'NO', 'Напряжение', 'Напряжение и ток', 'NO и NC', 'Ток'],
      dtype=object)